# Merge inventories
Objective: in top directory /data/KSC/EROSION/fromdropboxinventory/ copy files from 00_from_binary_files/ into 03_merge_inventories/ and then go through 01_from_processed_files/data_inventory.csv and copy any files not already in 00_from_binary_files/data_inventory.csv

In [ ]:
import header
paths = header.setup_environment()
for k,v in paths.items():
    print(k, '->', v)

import os
#import sys
#import glob
import pandas as pd

#import libWellData as LLE

# Generate complete list of TOB3 files (raw T   
INV1DIR = os.path.join(paths['new_data'], '00_from_binary_files')
INV2DIR = os.path.join(paths['new_data'], '01_from_processed_files')
OUTPUTDIR = os.path.join(paths['new_data'], '03_merge_inventories')
if not os.path.isdir(OUTPUTDIR):
    os.makedirs(OUTPUTDIR)
errorfile = os.path.join(OUTPUTDIR, '00_errors.txt')
os.system(f"echo path, error, processed >> {errorfile}")
INV1CSV = os.path.join(INV1DIR, f'data_inventory.csv')
INV2CSV = os.path.join(INV2DIR, f'data_inventory.csv')
OUTPUTCSV = os.path.join(OUTPUTDIR, f'data_inventory.csv')
MATCHCSV = OUTPUTCSV.replace('data_inventory', 'match')

allmasterrows=[]
allcolumns = []
lod = []

# Importing module
import shutil
if not os.path.isdir(OUTPUTDIR):
    shutil.copytree(INV1DIR, OUTPUTDIR)
else:
    os.system(f"rsync -av {INV1DIR}/* {OUTPUTDIR}/")



In [ ]:
# this piece of code will merge based on the contents of the relevant data_inventory.csv files.
# but those document the contents BEFORE the data are translated. we want them AFTER.
# so ignore this code, and instead go through all the files in the 01_processed_files directory, and inventory those first!

"""
from datetime import datetime
dfout = pd.read_csv(OUTPUTCSV, index_col=False)
dfinv2 = pd.read_csv(INV2CSV, index_col=False)
dfinv2['stime'] = [datetime.strptime(x, '%Y-%m-%d %H:%M:%S.%f') for x in dfinv2['starttime'] ]
dfinv2['etime'] = [datetime.strptime(x, '%Y-%m-%d %H:%M:%S.%f') for x in dfinv2['endtime'] ]
dfout['stime'] = [datetime.strptime(x, '%Y-%m-%d %H:%M:%S.%f') for x in dfout['starttime'] ]
dfout['etime'] = [datetime.strptime(x, '%Y-%m-%d %H:%M:%S.%f') for x in dfout['endtime'] ]
#dfout.rename(columns={'basename':'bname'}, inplace=True)
#dfinv2.rename(columns={'basename':'bname'}, inplace=True)

# now read rows of dfinv2 and see if they exist in dfout. if not, append them, and copy over the file
allrows = []
for idx, row in dfinv2.iterrows():
    try:
        #print(row['stime'], type(row['stime']))
        #querystr = f"uploadfolder=={row['uploadfolder']} and samprate=={row['samprate']} and seqno=={row['seqno']} and stime==\'{row['stime']}\' and etime==\'{row['etime']}\' "
        querystr = f"uploadfolder=={row['uploadfolder']} and samprate=={row['samprate']} and seqno=={row['seqno']} and basename==\'{row['basename']}\'"       
        #print(querystr)
        dfmatch = dfout.query(querystr)
    except Exception as e:
        print(querystr)
        #print(index)
        #print(index, row)
        continue
        break
    if len(dfmatch)==0:
        #print(idx, row['filename'], row['stime'], len(dfmatch) )
        #print(row)
        #print(dfmatch)
        allrows.append(row)

        # create output filename
        mybasename = row['basename'][:row['basename'].rfind(str(row['seqno']))]
        parentdir = row['sampratefolder']
        if not parentdir[0]=='B':
            parentdir = parentdir.lower()
        outdir = os.path.join(OUTPUTDIR, str(row['uploadfolder']), parentdir)
        outfile = mybasename + '_' + \
            row['stime'].strftime('%Y%m%d%H%M%S_') + \
            f"{int(row['seqno']):03d}" + \
            '.csv'
        outfullpath = os.path.join(outdir, outfile)
        print(outfullpath)
        
        if not os.path.isdir(outdir):
            os.makedirs(outdir)

        if not os.path.isfile(outfullpath):
            infile = os.path.join(row['topdir'], row['filename'])
            if os.path.isfile(infile):
                cmd = f"cp {infile} {outfullpath}"
                print(cmd)
                os.system(cmd)

        

    #outfile = os.path.join(OUTPUTDIR, row['uploadfolder'], row['sampratefolder'], f"{row['bname']}_ + )
    #if idx>10:
    #    break
alldf = pd.DataFrame(allrows)
print(alldf)
alldf.to_csv(MATCHCSV, index=False)
"""

In [ ]:

import libWellData as LLE
import importlib
importlib.reload(LLE)

# Generate complete list of TOB3 files (raw TOB3 files from CS dataloggers)
processed_files = sorted(LLE.list_loggernet_csv_files(INV2DIR))
print(f'Found {len(processed_files)} Processed files')
missing = 0
for thisfile in processed_files:
    #print(thisfile)
    destfile = thisfile.replace(INV2DIR, OUTPUTDIR).replace('xxx', 'x').replace('xx', 'x').replace('x.csv', '.csv').replace('_REVERSED', '')
    #print(destfile)
    if os.path.isfile(destfile):
        pass
        #print(thisfile, '\t->\t', destfile, end='')
        #print(' - exists')
    else:
        #pass
        print(thisfile, '\t->\t', destfile, end='')
        print(' - not found')
        missing+=1
        destdir = os.path.dirname(destfile)
        if not os.path.isdir(destdir):
            os.makedirs(destdir)
        try:
            os.system(f"cp {thisfile} {destfile}")
        except Exception as e:
            print(e)
            raise('farted!')
print(f'This would add {missing} missing files')

In [78]:
allfiles = sorted(LLE.list_loggernet_csv_files(OUTPUTDIR))
print(f'Found {len(allfiles)} files overall')
lod = []
for thisfile in allfiles:
    filebase = os.path.basename(thisfile)
    pathparts = thisfile.split('/')
    uploaddir = pathparts[-3]
    sampratedir = pathparts[-2]
    thisdf = pd.read_csv(thisfile, nrows=1, index_col=False)
    row = thisdf.iloc[0]
    row['uploaddate']=uploaddir
    row['subdir']=sampratedir
    row['basename']=filebase
    if '.' in row['TIMESTAMP']:
        row['TIMESTAMP'] = datetime.strptime(row['TIMESTAMP'], '%Y-%m-%d %H:%M:%S.%f')
    else:
        row['TIMESTAMP'] = datetime.strptime(row['TIMESTAMP'], '%Y-%m-%d %H:%M:%S')
    lod.append(row)
    #print(row)
dfall = pd.DataFrame(lod)

dfall.sort_values(by='TIMESTAMP').to_csv(os.path.join(OUTPUTDIR, 'all2.csv'))



Found 2273 files overall


/tmp/ipykernel_3454871/312014135.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['uploaddate']=uploaddir
/tmp/ipykernel_3454871/312014135.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['uploaddate']=uploaddir
/tmp/ipykernel_3454871/312014135.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['subdir']=sampratedir
/tmp/ipykernel_3454871/312014135.py:12: SettingWithCopyWarning: 
A value is trying to be set on a c